In [1]:
import tensorflow as tf

In [2]:
gpus = tf.config.experimental.list_physical_devices('GPU')
tf.config.experimental.set_memory_growth(gpus[0], True)

In [3]:
import os
import matplotlib.pyplot as plt
import numpy as np
import network
from data_pipeline import set_up_data_pipeline, decode, augment
from params import patches_root, train_db_path, test_db_path
from tensorflow.keras.preprocessing.image import ImageDataGenerator
from tensorflow.keras.callbacks import ModelCheckpoint, EarlyStopping, Callback

In [4]:
img_height = 256
img_width = 256
batch_size = 64

In [5]:
# Load the training and validation datasets

train_generator = ImageDataGenerator(preprocessing_function=None,
    rescale=1./255, horizontal_flip=True, vertical_flip=True)

validation_generator = ImageDataGenerator(preprocessing_function=None,
    rescale=1./255)

train_data_gen  = train_generator.flow_from_directory(
    directory=r"./patches/train/",
    target_size=(img_width, img_height), color_mode='grayscale',
    batch_size=batch_size, class_mode="categorical", shuffle=True)

validation_data_gen = validation_generator.flow_from_directory(
    directory=r"./patches/test/",
    target_size=(img_width, img_height), color_mode='grayscale',
    batch_size=batch_size, class_mode="categorical", shuffle=True)

Found 46725 images belonging to 8 classes.
Found 11675 images belonging to 8 classes.


In [6]:
print("Num GPUs Available: ", len(tf.config.experimental.list_physical_devices('GPU')))

Num GPUs Available:  1


In [7]:
print("[*] Define model")
model = network.build()

[*] Define model
Model: "sequential"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
conv2d (Conv2D)              (None, 256, 256, 3)       78        
_________________________________________________________________
conv2d_1 (Conv2D)            (None, 128, 128, 96)      14208     
_________________________________________________________________
batch_normalization (BatchNo (None, 128, 128, 96)      384       
_________________________________________________________________
activation (Activation)      (None, 128, 128, 96)      0         
_________________________________________________________________
max_pooling2d (MaxPooling2D) (None, 64, 64, 96)        0         
_________________________________________________________________
conv2d_2 (Conv2D)            (None, 64, 64, 64)        153664    
_________________________________________________________________
batch_normalization_1 (Batch (None, 64,

In [8]:
sgd = tf.optimizers.SGD(lr=0.001, momentum=0.9, decay=0.0005)
model.compile(
    optimizer=sgd, 
    loss='categorical_crossentropy', 
    metrics=['accuracy'])

In [9]:
#           ------------ Train the Model ------------
ConstrainLayer = network.ConstrainLayer(model)
callbacks = [ModelCheckpoint('./saved_model/weights.{epoch:02d}.h5',
    monitor='acc',verbose=1, save_best_only=False,
    save_freq=1), ConstrainLayer]

history = model.fit_generator(generator=train_data_gen, epochs=45, 
     callbacks=callbacks)  #removed validation data

Epoch 1/45

Epoch 00001: saving model to ./saved_model/weights.01.h5
  1/731 [..............................] - ETA: 39:09 - loss: 2.5649 - accuracy: 0.1406
Epoch 00001: saving model to ./saved_model/weights.01.h5
  2/731 [..............................] - ETA: 21:24 - loss: 2.5484 - accuracy: 0.0938
Epoch 00001: saving model to ./saved_model/weights.01.h5
  3/731 [..............................] - ETA: 15:30 - loss: 2.4420 - accuracy: 0.0990
Epoch 00001: saving model to ./saved_model/weights.01.h5
  4/731 [..............................] - ETA: 12:31 - loss: 2.3864 - accuracy: 0.1055
Epoch 00001: saving model to ./saved_model/weights.01.h5
  5/731 [..............................] - ETA: 10:37 - loss: 2.3306 - accuracy: 0.1187
Epoch 00001: saving model to ./saved_model/weights.01.h5
  6/731 [..............................] - ETA: 9:22 - loss: 2.3012 - accuracy: 0.1406 
Epoch 00001: saving model to ./saved_model/weights.01.h5
  7/731 [..............................] - ETA: 8:27 - loss: 

In [10]:
#           ------------------------------------------

# Next thing that could be implemented is the 'Extremely Randomized 
# Trees Classifier" used to extract the 1x200 vector which contains
# the Deep Convolutional Features. It is reported that this provides
# a small improvement in the model's accuracy.

# The following line makes sure that the program exits successfully every 
# time. It deals with the "Exception ignored in BaseSession" bug. Not of 
# importance anyway.
import gc; gc.collect()

34